<a href="https://colab.research.google.com/github/aditya-007/BESS_optimization/blob/main/Dispatch_optimization_2020_v1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Battery dispatch optimization
The goal of this exercise is to optimize the charge/discharge behavior of a battery system performing energy arbitrage in the NYISO market. The model objective is to maximize revenue over a year and the project objective is to gain insights into market dynamics and expected system behavior. We have hourly LBMP data for the entire year (taken from 2017), which we assume is accurate with perfect foresight.

The battery system has maximum storage capacity of 200 kWh and a power rating of 100 kW (charge and discharge). Round-trip AC-AC efficiency is 85%. The maximum daily discharge throughput is constrained to 200 kWh within a 24-hour period.

Because we are using this model to understand the market dynamics in the NYISO NYC hub, it's fine to run the entire year optimzation at once rather than running in discrete periods. When actually operating the battery we would need to use price forecasts that would become less accurate over time. In that situation a series of multi-day optimizations would be used. The first window would assume a starting charge state (I'm using half of the manimum charge in this exercise), and might predict 3-4 days. The first 24-hours would be kept and used as a constraint in the next period. For the second period, a window of 4-5 days would be used -- values from the first day would be used to constrain hours 0-23, and the optimization would again use a look-ahead of 2-3 days to ensure accurate model behavior. This cycle (keep 24 hours and use then as a constrain in the next iteration) would then continue through the end of the year.

I've elected to stick with the simplier approach here because it is easier/faster to code and should provide the same optimized dispatch results. Actually optimizing dispatch for a battery system would require forecasting prices. Because this is a much simpler exercise a simpler model that takes less time to build is fine.

In [ ]:
pip install -r requirements.txt

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 49.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 48.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.1/117.1 kB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 kB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 383.4/383.4 kB 32.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.4/59.4 kB 7.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.2/190.2 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.1/12.1 MB 73.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 10.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 69.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
!pip install -q pyomo

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 27.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 6.1 MB/s eta 0:00:00


In [ ]:
!apt-get install -y -qq glpk-utils

Selecting previously unselected package libsuitesparseconfig5:amd64.
(Reading database ... 121913 files and directories currently installed.)
Preparing to unpack .../libsuitesparseconfig5_1%3a5.10.1+dfsg-4build1_amd64.deb ...
Unpacking libsuitesparseconfig5:amd64 (1:5.10.1+dfsg-4build1) ...
Selecting previously unselected package libamd2:amd64.
Preparing to unpack .../libamd2_1%3a5.10.1+dfsg-4build1_amd64.deb ...
Unpacking libamd2:amd64 (1:5.10.1+dfsg-4build1) ...
Selecting previously unselected package libcolamd2:amd64.
Preparing to unpack .../libcolamd2_1%3a5.10.1+dfsg-4build1_amd64.deb ...
Unpacking libcolamd2:amd64 (1:5.10.1+dfsg-4build1) ...
Selecting previously unselected package libglpk40:amd64.
Preparing to unpack .../libglpk40_5.0-1_amd64.deb ...
Unpacking libglpk40:amd64 (5.0-1) ...
Selecting previously unselected package glpk-utils.
Preparing to unpack .../glpk-utils_5.0-1_amd64.deb ...
Unpacking glpk-utils (5.0-1) ...
Setting up libsuitesparseconfig5:amd64 (1:5.10.1+dfsg-4b

In [ ]:
import pandas as pd
from pathlib import Path
import altair as alt

In [ ]:
def read_excel_to_df(path):
    """
    Read an Excel file with pandas and store the data in a DataFrame.

    Parameters
    ----------
    path : str or other object for read_excel filepath parameter
        Path to Excel file with data

    Returns
    -------
    DataFrame
        df with data from the Excel file
    """

    df = pd.read_excel(path)
    return df

In [ ]:
import numpy as np
from pyomo.environ import *

In [ ]:
from datetime import datetime, timedelta

In [ ]:
def model_to_df(model, first_hour, last_hour, start_time='2020-01-01 00:00:00'):
    """
    Create a dataframe with hourly charge, discharge, state of charge, and
    price columns from a pyomo model. Only uses data from between the first
    (inclusive) and last (exclusive) hours.

    Parameters
    ----------
    model : pyomo model
        Model that has been solved

    first_hour : int
        First hour of data to keep
    last_hour: int
        The final hour of data to keep

    Returns
    -------
    dataframe

    """
    # Need to increase the first & last hour by 1 because of pyomo indexing
    # and add 1 to the value of last model hour because of the range
    # second model hour by 1
    hours = range(model.T[first_hour+1], model.T[last_hour+1]+1)
    Ein = [value(model.Ein[i]) for i in hours]
    Eout = [value(model.Eout[i]) for i in hours]
    price = [model.P.extract_values()[None][i] for i in hours]
    #output = [model.O.extract_values()[None][i] for i in hours]
    output = [model.O[i] for i in hours]
    charge_state = [value(model.S[i]) for i in hours]

    # Generate timestamps
    start_datetime = datetime.strptime(start_time, '%Y-%m-%d %H:%M:%S')
    timestamps = [start_datetime + timedelta(hours=i) for i in hours]

    df_dict = dict(
        hour=hours,
        timestamp=timestamps,
        Ein=Ein,
        Eout=Eout,
        price=price,
        output=output,
        charge_state=charge_state
    )

    df = pd.DataFrame(df_dict)

    return df

In [ ]:
def optimize_year(df, first_model_hour=0, last_model_hour=8783):
    """
    Optimize the charge/discharge behavior of a battery storage unit over a
    full year. Assume perfect foresight of electricity prices. The battery
    has a discharge constraint equal to its storage capacity and round-trip
    efficiency of 85%.

    Parameters
    ----------
    df : dataframe
        dataframe with columns of hourly LBMP and the hour of the year
    first_model_hour : int, optional
        Set the first hour of the year to be considered in the optimization
        (the default is 0)
    last_model_hour : int, optional
        Set the last hour of the year to be considered in the optimization (the
        default is 8759)

    Returns
    -------
    dataframe
        hourly state of charge, charge/discharge behavior, lbmp, and time stamp
    """

    #Filter the data
    df = df.loc[first_model_hour:last_model_hour, :]

    model = ConcreteModel()

    # Define model parameters
    model.T = Set(doc='hour of year', initialize=df.Hour.tolist(), ordered=True)
    model.Rmax = Param(initialize=50,
                       doc='Max rate of power flow (MW) in or out')
    model.Smax = Param(initialize=200, doc='Max storage (kWh)')
    model.Dmax = Param(initialize=200, doc='Max discharge in 24 hour period')
    model.P = Param(initialize=df.Price.tolist(), doc='Price for each hour')
    model.O = Param(model.T, initialize=df.Power.tolist(), doc='Output of the plant (MW)')
    eta = 0.85 # Round trip storage efficiency

    # Charge, discharge, and state of charge
    # Could use bounds for the first 2 instead of constraints
    model.Ein = Var(model.T, domain=NonNegativeReals)
    model.Eout = Var(model.T, domain=NonNegativeReals)
    model.S = Var(model.T, bounds=(0, model.Smax))


    #Set all constraints
    def storage_state(model, t):
        'Storage changes with flows in/out and efficiency losses'
        # Set first hour state of charge to half of max
        if t == model.T.first():
            return model.S[t] == model.Smax / 2
        else:
            return (model.S[t] == (model.S[t-1]
                                + (model.Ein[t-1] * np.sqrt(eta))
                                - (model.Eout[t-1] / np.sqrt(eta))))

    model.charge_state = Constraint(model.T, rule=storage_state)

    def discharge_constraint(model, t):
        "Maximum dischage within a single hour"
        return model.Eout[t] <= model.Rmax

    model.discharge = Constraint(model.T, rule=discharge_constraint)

    def charge_constraint(model, t):
        "Maximum charge within a single hour"
        out = model.O[t]
        return model.Ein[t] <= min(model.Rmax, out)

    model.charge = Constraint(model.T, rule=charge_constraint)

    # Without a constraint the model would discharge in the final hour
    # even when SOC was 0.
    def positive_charge(model, t):
        'Limit discharge to the amount of charge in battery, including losses'
        return model.Eout[t] <= model.S[t] / np.sqrt(eta)
    model.positive_charge = Constraint(model.T, rule=positive_charge)

    def discharge_limit(model, t):
        "Limit on discharge within a 24 hour period"
        max_t = model.T.last()

        # Check all t until the last 24 hours
        # No need to check with < 24 hours remaining because the constraint is
        # already in place for a larger number of hours
        if t < max_t - 24:
            return sum(model.Eout[i] for i in range(t, t+24)) <= model.Dmax
        else:
            return Constraint.Skip

    model.limit_out = Constraint(model.T, rule=discharge_limit)

    # Define the battery income, expenses, and profit
    income = sum(df.loc[t, 'Price'] * model.Eout[t] for t in model.T)
    expenses = sum(df.loc[t, 'Price'] * model.Ein[t] for t in model.T)
    profit = income - expenses
    model.objective = Objective(expr=profit, sense=maximize)

    # Solve the model
    solver = SolverFactory("glpk",executable='/usr/bin/glpsol')
    solver.solve(model)

    results_df = model_to_df(model, first_hour=first_model_hour,
                             last_hour=last_model_hour)

    return results_df

In [ ]:

# Select your appropriate notebook type for rendering Altair figures
alt.renderers.enable('jupyterlab')
# alt.renderers.enable('notebook')
alt.data_transformers.enable('default', max_rows=None)


DataTransformerRegistry.enable('default')

## Read data
Functions to read data and run the optimization model are provided in scripts in the `src` folder. The `read_all_nyc` function combines data from daily .csv files, filters out all non-NYC node prices, and renames the columns to snake case.

In [ ]:
data_path = 'PowerOutput.xlsx'

df = read_excel_to_df(data_path)

In [ ]:
df.head()

Hour  Price  Power
0     0     42    0.0
1     1     39    0.0
2     2     37    0.0
3     3     32    0.0
4     4     31    0.0

## Model parameters and constraints

**Parameters**
- $t$: timestep or hour
- $R_{max}$ (100 kW): maximum power than can be delivered to or from the battery (charge or discharge rate)
- $S_{max}$ (200 kWh): maximum battery capacity
- $S_t$: storage at time $t$
- Eff ($\eta$) (85%): efficiency
- $D_{max}$ (200 kWh): max discharge within a 24 hour period
- $P_t$: LBMP at time $t$

**Decision variables**
- $E^{in}_t$: energy delivered to the battery at time $t$
- $E^{out}_t$: energy discharged from the battery at time $t$

**Constraints**
- $S_1$ = $\frac{S_{max}}{2}$ (Assume storage begins at half of capacity)
- $S_t$ = $S_{t-1} + \sqrt{\eta} \times E^{in}_{t-1} - \frac{E^{out}_{t-1}}{\sqrt{\eta}}$
- $\forall t, S_t \geq 0$
- $\forall t, S_t \leq S_{max}$
- $\forall t, E^{in}_t \leq R_{max}$
- $\forall t, E^{out}_t \leq R_{max}$
- $\forall t, E^{out}_t \leq S_t$
- $\sum_{t'=t-23}^t E^{out}_{t'} \leq D_{max} \forall t \subset (T, t \geq 24)$

## Run the optimization model
The `optimize_year` function takes in the LBMP data from our new dataframe and returns the optimization results in a dataframe.

In [ ]:
results_df = optimize_year(df)

position is deprecated.  Please use at()  (deprecated in 6.1, will be
removed in (or after) 7.0)
(called from <ipython-input-83-2e7ff8ec7e38>:25)


In [ ]:
results_df.head()

hour           timestamp  Ein       Eout  price  output  charge_state
0     0 2020-01-01 00:00:00  0.0  50.000000     42     0.0    100.000000
1     1 2020-01-01 01:00:00  0.0  42.195445     39     0.0     45.767386
2     2 2020-01-01 02:00:00  0.0   0.000000     37     0.0      0.000000
3     3 2020-01-01 03:00:00  0.0   0.000000     32     0.0      0.000000
4     4 2020-01-01 04:00:00  0.0   0.000000     31     0.0      0.000000

### Output results

In [ ]:
from google.colab import files

In [ ]:
results_df.to_csv('full_year_optimization_results1.csv')

In [ ]:
files.download('full_year_optimization_results1.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Analysis of results
In this exercise I've been asked to present the following:
- Summary values
    - Annual revenue
    - Annual charging costs
    - Annual discharged throughput
- Plots
    - Hourly dispatch and LBMP for the most profitable week (assuming calendar week)
    - Total profit for each month

### Summary values
Revenue, costs, and profit still need to be calculated using energy in/out and the hourly price

In [ ]:
# Results
results_df['revenue'] = results_df.Eout * results_df.price
results_df['charge_cost'] = results_df.Ein * results_df.price
results_df['profit'] = results_df.revenue - results_df.charge_cost

In [ ]:
total_revenue = results_df.revenue.sum()
total_charge_cost = results_df.charge_cost.sum()
total_discharge = results_df.Eout.sum()
total_profit = results_df.profit.sum()

print('Annual revenue was €{:,.2f}'.format(total_revenue))
print('Annual charging cost was €{:,.2f}'.format(total_charge_cost))
print('Annual profit was €{:,.2f}'.format(total_profit))
print('Annual discharged throughput was {:,.2f} MWh'.format(total_discharge))

Annual revenue was €1,498,290.42
Annual charging cost was €1,144,725.86
Annual profit was €353,564.55
Annual discharged throughput was 37,574.56 MWh


### Figures

In [ ]:
results_df['week'] = results_df.timestamp.dt.week
results_df['month'] = results_df.timestamp.dt.month
results_df['hour_of_day'] = results_df.timestamp.dt.hour

<ipython-input-93-bb36ff41049c>:1: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated. Please use Series.dt.isocalendar().week instead.
  results_df['week'] = results_df.timestamp.dt.week


After dropping the first day of 2017 (which was a Sunday, and part of the 52nd week of 2016), the most profitable week was the last week of the year.

In [ ]:
profit_weekly = results_df.loc[results_df.timestamp >= '2020-01-01', :].groupby('week')['profit'].sum()


In [ ]:
print(profit_weekly)

week
1      7410.237886
2      8607.488423
3     -3451.340518
4      6630.387887
5      4582.730827
6      6135.190986
7      5712.996804
8     10408.105676
9      8245.942735
10     6252.224575
11    10126.597716
12     1009.873610
13     7169.388920
14     5231.406647
15     8989.627298
16     7496.338381
17     8820.573476
18     9604.655809
19     4322.115639
20     4955.115873
21     7844.196384
22     1465.089592
23     8345.893851
24     4858.495077
25     3764.539100
26     4196.918919
27     6662.312526
28     6303.359534
29      375.421520
30     4751.276761
31     1241.547650
32     3287.256735
33     6051.937677
34     5589.388422
35     6817.132933
36    10569.508711
37     3110.053180
38     2247.701259
39    12900.886945
40    16068.346132
41    14695.461497
42    11647.114580
43    10239.352575
44     8513.189209
45     3633.880539
46     9004.325002
47     3539.661323
48     4655.260200
49    12520.758434
50    -2112.293576
51     3196.806003
52    20533.658311
53     

In [ ]:
results_df.loc[results_df.timestamp >= '2020-01-01', :].groupby('week')['profit'].sum().idxmax()

52

Including both the dispatch and hourly LBMP in a single plot is difficult because their values have different scales (dispatch is capped at 100 kWh while LBMP in week 52 goes over \\$200/kWh). A dual y-axis plot can be difficult to read, so I've decided to show one plot on top of the other. The plot of LBMP uses color to encode dispatch, which helps to make the whole thing easier to interprete.

In [ ]:
alt.renderers.enable('colab')

RendererRegistry.enable('colab')

In [ ]:
data = results_df.loc[(results_df.timestamp >= '2020-01-01') &
                      (results_df.week == 52), :].copy()
data.loc[:, 'dispatch'] = data.Ein - data.Eout
dispatch_data = pd.melt(data, id_vars='timestamp', value_vars=['Eout', 'Ein'], var_name='Dispatch')

color_scale = alt.Scale(
            domain=['Ein', 'Eout'],
            range=['#f99820', '#2081f9']
        )

dispatch = alt.Chart(dispatch_data).mark_line().encode(
    x='timestamp:T',
    y=alt.Y('value:Q', axis=alt.Axis(title='Electricity in/out (MWh)')),
    color=alt.Color('Dispatch:N', scale=color_scale)
).properties(
    height=400,
    width=800
)

price = alt.Chart(data).mark_circle().encode(
    x='timestamp:T',
    y=alt.Y('price:Q', axis=alt.Axis(title='Electricity Price (€)')),
    color=alt.Color('dispatch:Q', scale=alt.Scale(scheme='blueorange')),
    tooltip='dispatch:Q'
).properties(
    height=400,
    width=800
)

alt.vconcat(
    dispatch,
    price
)

alt.VConcatChart(...)

In [ ]:
# Create Altair chart
alt.Chart(results_df).mark_line().encode(
    x='week:O',  # 'week' column as ordinal (categorical) for x-axis
    y='sum(profit):Q',  # 'profit' column as quantitative (numerical) for y-axis
    color=alt.condition(
        alt.datum['sum(profit)'] < 0,  # Condition for negative values
        alt.value('red'),  # Color for negative values
        alt.value('green')  # Default color for non-negative values
    )
).properties(
    height=300,
    width=800
)

alt.Chart(...)

In [ ]:
# Group by month and calculate the total profit for each month
profit_monthly = results_df.loc[results_df.timestamp >= '2020-01-01', :].groupby('month')['profit'].sum()

# Rename the columns for clarity
profit_monthly_df = profit_monthly.to_frame()

# Display the table
profit_monthly_df

profit
month              
1      26073.166344
2      27476.249406
3      24884.629778
4      34805.094926
5      24329.804174
6      26994.346947
7      18510.650353
8      19540.483406
9      31908.916907
10     59753.167255
11     25362.656991
12     33925.387768

In [ ]:
alt.Chart(results_df).mark_line().encode(
    x='month:O',
    y='sum(profit):Q'
).properties(
    height=300,
    width=500
)

alt.Chart(...)